In [1]:
############################################################################################################################ 
# Get the latest CREST files for each ID within the target folder (dirname)

from pathlib import Path
import json
from sqlite3 import connect as sqlite3_connect
from sqlite3 import DatabaseError
from igraph import Graph as ig_Graph
from igraph import plot as ig_plot
from scipy.spatial.distance import cdist
import random
from random import choice as random_choice
from itertools import combinations
import itertools
from numpy import array, unravel_index, argmin, mean,unique
import matplotlib
import pandas as pd
import numpy as np
from copy import deepcopy
from datetime import datetime
from time import time, sleep
import neuroglancer
from webbrowser import open as wb_open
from webbrowser import open_new as wb_open_new
import matplotlib.pyplot as plt
import seaborn as sns
import cloudvolume as cv
import trimesh

from eCREST_cli import ecrest, import_settings, get_cell_filepaths

Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.


In [2]:
efish_cloudvolume = cv.CloudVolume('gs://fish-ell/roi450um_seg32fb16fb_220930', progress=True)

In [3]:
path_to_settings_json = '/Users/kperks/Documents/ell-connectome/eCREST-local-files/settings_dict.json'
settings_dict = import_settings(path_to_settings_json)

db_cursors = sqlite3_connect(settings_dict['db_path'], check_same_thread=False).cursor()

a = ', '.join(['base_address'])

db_cursors.execute(f'''SELECT {a} FROM addresses_table LIMIT 1''')

[base_seg] = db_cursors.fetchall()[0]

mesh_seg = 'precomputed://gs+ngauth+https://ngauth-goog.appspot.com/fish-ell/roi450um_seg32fb16fb_220930'

In [4]:
path_to_settings_json = '/Users/kperks/Documents/ell-connectome/eCREST-local-files/settings_dict.json'
settings_dict = import_settings(path_to_settings_json)

dirpath = Path(settings_dict['save_dir'])

nodefiles = get_cell_filepaths(dirpath)
                    

In [5]:
all_cells = [126618353, 127870654, 128737253, 128813171, 213501262, 213590737,
       213669553, 213760634, 299439953, 299530386, 472175645,
       472409584, 473647416, 557092670, 558360429, 642905044, 644005141,
       644143297]

In [ ]:
# all_cells = [137991336] 
savepath = Path('/Users/kperks/Library/CloudStorage/GoogleDrive-kperky@gmail.com/.shortcut-targets-by-id/16q1BuOMfD2ta0Cwq8CjMlRe4rDvbuWC5/ELL_connectome/Krista/blender/lf_393325331_inputs')

reduction_ratio = 0.2

scale_factor = 100000
yaxis_replace_scale = 32768*16/scale_factor
refpt = [0,0,0]

for focal_cell_id in all_cells:
    dirpath = Path(settings_dict['save_dir'])
    focal_cell_fname = nodefiles[str(focal_cell_id)]#'cell_graph_214581797__2023-07-17 12.58.20.json'
    
    cell = ecrest(settings_dict,filepath = dirpath / focal_cell_fname, launch_viewer=False)

    mesh_ids = [bs for dtype in cell.cell_data['base_segments'].keys() for bs in cell.cell_data['base_segments'][dtype]]
   
    # grab the mesh for more than one object
    # Initialize an empty Trimesh object
    fused_mesh = trimesh.Trimesh()
    
    for id in mesh_ids:
      mesh = efish_cloudvolume.mesh.get(int(id))
      vertices = list(mesh.values())[0].vertices
      vertices = vertices/scale_factor
      vertices = [[v[0]-refpt[0],v[1]-refpt[1],v[2]-refpt[2]] for i,v in enumerate(vertices)]
      vertices = [[v[0],yaxis_replace_scale-v[1],v[2]] for v in vertices]
      faces = list(mesh.values())[0].faces
      trimesh_mesh = trimesh.Trimesh(vertices=vertices, faces=faces,process=True)
    
      # downsample the fused mesh before joining to the fused_mesh and exporting as a .obj for blender
      simplified_mesh = trimesh_mesh.simplify_quadric_decimation(face_count=len(trimesh_mesh.vertices) * reduction_ratio)
      fused_mesh = trimesh.util.concatenate([fused_mesh, simplified_mesh])
    
    # prompt: downsample the fused mesh before exporting as a .obj for blender
    # reduction_ratio = 0.2
    # simplified_mesh = fused_mesh.simplify_quadric_decimation(face_count=len(fused_mesh.vertices) * reduction_ratio)
    
    
    fused_mesh.export(savepath / f'mg1_{focal_cell_id}.obj');

100%|███████████████████████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00,  6.17it/s]

In [23]:
savepath / f'{focal_cell_id}.obj'

PosixPath('/Users/kperks/Library/CloudStorage/GoogleDrive-kperky@gmail.com/.shortcut-targets-by-id/16q1BuOMfD2ta0Cwq8CjMlRe4rDvbuWC5/ELL_connectome/Krista/blender/50705075.obj')